In [1]:
!pip -q install git+https://github.com/huggingface/transformers.git
!pip -q install peft
!pip -q install accelerate
!pip -q install sentencepiece
!pip -q install bitsandbytes

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 78.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 1.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 17.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 9.0 MB/s eta 0:00:00


In [2]:
from IPython.display import Markdown as md

import transformers
import peft
import accelerate
import bitsandbytes

print(transformers.__version__)
print(peft.__version__)
print(accelerate.__version__)



===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('8013'), PosixPath('http'), PosixPath('//172.28.0.1')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc483011

4.29.0.dev0
0.2.0
0.18.0


In [3]:
import torch
from peft import PeftModel
from transformers import LlamaTokenizer, LlamaForCausalLM

def load_model(base, finetuned):
    tokenizer = LlamaTokenizer.from_pretrained(base)
    tokenizer.pad_token_id = 0
    tokenizer.padding_side = "left"

    model = LlamaForCausalLM.from_pretrained(
        base,
        load_in_8bit=True,
        device_map="auto",
    )
    
    model = PeftModel.from_pretrained(
        model, 
        finetuned,
        device_map={'': 0}
    )
    return model, tokenizer

def get_output_batch(
    model, tokenizer, prompt, generation_config, device='cuda'
):
  encoding = tokenizer(prompt, return_tensors="pt")
  input_ids = encoding["input_ids"].to(device)
  generated_id = model.generate(
      input_ids=input_ids,
      generation_config=generation_config,
  )

  decoded = tokenizer.batch_decode(
      generated_id, skip_prompt=True, skip_special_tokens=True
  )
  del input_ids, generated_id
  torch.cuda.empty_cache()
  return decoded[0].split("### Response:")[-1]

### AlpacaGPT4-LoRA 7B (05/01)

In [14]:
from transformers import GenerationConfig

base = "elinas/llama-7b-hf-transformers-4.29"
sft = "LLMs/AlpacaGPT4-LoRA-7B-elina"

genConfig = GenerationConfig(
    temperature=0.95,
    top_p=0.9,
    top_k=50,
    num_beams=1,
    repetition_penalty=1.2,
    max_new_tokens=1024,
    do_sample=True,
)

In [6]:
model, tokenizer = load_model(base, sft)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [16]:
prompt = """### Instruction: Compose an engaging travel blog post about a recent trip to Hawaii, highlighting cultural experiences and must-see attractions.

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Greetings from the tropical paradise of Maui! Let me take you on an adventure through one of the world's most enchanting destinations - Hawaii Island. My name is Jenny Chupeco and I am a travel blogger who loves sharing my journeys with like minded people around the globe.  This beautiful island has something for everyone in store, whether it be surfing, hiking or simply lounging at the beach – there’s no lack of activities here. Today, let us explore some of its rich culture, cuisine and history that makes this place so unique and memorable.<br /><br />Hawaiians are well known for their warm hospitality and traditions, often referred to as “aloha spirit”. It can be seen everywhere in small gestures such as greeting someone by saying “Aloha” which translates into “hello” but means much more than just “hi”, inviting them to relax and enjoy themselves. The local population takes great pride in preserving their customs and traditions throughout generations.<br />One way visitors experience aloha is during traditional dance performances called “hula”. Hulas were originally created many

In [17]:
prompt = """### Instruction: Can you help me write a formal email to a potential business partner proposing a joint venture?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Prospective Business Partner],<br /> <br />Thank you for your interest in our proposed partnership. We at Company X have been contemplating the possibility of entering into a Joint Venture with another organization, and we believe that our respective strengths could make us formidable allies on any project or opportunity that comes up. Our core competencies include expertise in technology development, operations management, market research, and strategic planning, all areas which would greatly benefit from your experience as an innovator in manufacturing, supply chain logistics, and product design. By joining forces, we can leverage each other's resources to achieve mutual growth and success.<br /><br />As such, we are seeking your input regarding specific details about the nature of this potential partnership including goals, objectives, timelines, roles and responsibilities, risk-sharing arrangements, funding sources, governance structures, etc., so that we may better assess whether there is alignment between our interests before making further plans towards establishing a strong working relationship. Thank you again for considering our proposal; if anything further is needed, please do not hesitate to let us know.

In [18]:
prompt = """### Instruction: Can you help me write a resignation letter to my current employer, while leaving on good terms and expressing gratitude for the opportunities provided?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 Dear [Current Employer], <br /><br />After careful consideration I have decided that it is in both our best interests if I move on from this position. During my time here at [Company Name] I have gained valuable experience working with great people such as yourself who helped guide me throughout my tenure. Although this decision was not an easy one for me, I feel confident moving forward into something new where my skills will be better utilized.<br /><br />It has been a pleasure working alongside you, and I would like to thank you personally for your support during these past months. I wish you continued success and professional growth within the organization, and know that we'll stay connected even after my departure date.

In [19]:
prompt = """### Instruction: How can you determine if a restaurant is popular among locals or mainly attracts tourists, and why might this information be useful?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />If a restaurant is mostly patronized by local residents as opposed to international visitors, it likely means that the food has been highly rated for its authenticity. Local restaurants are often more well-known amongst their neighborhood's population because of personal recommendations from friends and family. These establishments also have an advantage when it comes to pricing and value, which makes them more affordable than other options catering to outsiders. Additionally, most travelers seek out unique dining experiences in new cities rather than trying to recreate what they know back home. By identifying whether a restaurant caters primarily towards locals versus tourists, one could deduce that certain items on the menu may not contain ingredients commonly found elsewhere but would still appeal to visitors due to familiar flavors. This can create a richer culinary experience while giving guests a taste of traditional cuisine within their destination.

In [20]:
prompt = """### Instruction: What are some subtle clues that suggest someone is pretending to understand a topic or conversation when they are actually confused or uninformed?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 1. The person repeats the same question multiple times, without fully understanding it after being given an explanation once beforehand. This suggests that their confusion may be deliberate and that they are attempting to feign knowledge in order to appear informed while not truly comprehending what is going on. They may also use phrases such as "I don't know but..." suggesting an attempt to pass themselves off as knowledgeable but unable to provide any concrete information due to their lack of expertise. In this case, it is important for others to ask follow-up questions if needed until clarification can be reached rather than simply taking the first answer at face value.<br />2. Evidence of research conducted online prior to the discussion shows that the individual has been looking up specific terms associated with the subject matter in preparation for the chat. However, if there are inconsistencies between how those terms have been defined by other sources compared to how the person defines them during the chat session, then it could indicate that he/she was only using those terms out of context in hopes of appearing more knowledgeable about the topic.<br />3. While asking seemingly well thought out questions, the response received indicates no real effort behind their lines. Instead, their answers come across as

In [21]:
prompt = """### Instruction: What are some potential implications of using a single-use plastic bottle versus a reusable bottle on both the environment and human health?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 <br />Using a single use plastics bottles has several potential impacts in regards to environmental concerns as well as human health. A few examples include:<br />1) Single Use Plastic Bottles create litter, clogging our rivers, oceans, landfills and polluting habitats for animals such as sea turtles who mistake them for jellyfish or other food sources that have led to their decline in populations due to ingestion. It also creates waste which is not biodegradable and poses an extended threat to wildlife by providing breeding grounds for mosquitoes etc., contributing to global warming through greenhouse gas emissions from incineration and degrades water quality causing eutrophication leading to harmful algal blooms (HAB).<br />2) Reusing a metal stainless steel can significantly reduce these negative effects compared with disposing it after just one use. This will prevent further contamination and waste creation. Moreover, reducing the need for new raw materials required for manufacturing more single-use products saves energy, and reduces carbon dioxide (CO2), methane (CH4), and nitrous oxides (N2O) –

In [22]:
prompt = """### Instruction: What factors would you consider when designing an inclusive and accessible public transportation system?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 <br />1. Accessibility for all modes of transport - including walking, biking, driving, buses, trains etc., ensuring that everyone can reach the destination with ease.<br />2. Inclusiveness - providing equal access to people with disabilities or other limitations. This could include ramps on bus stops or lifts at train stations, braille signs in subway tunnels, audible announcements at busy transit hubs, handicapped parking spots near entrances.<br />3. Communications - providing clear and reliable information about route schedules, delays, changes and emergencies to users across different channels such as audio alert systems, text message updates, digital kiosks or customer service centers.<br />4. Safety – using surveillance cameras, anti-graffiti paint, CCTV security systems to reduce instances of crime, harassment or accidents within the transit environment.